In [10]:
from itertools import zip_longest
from pathlib import Path
from freespeech.types import Event, Voice
from freespeech.lib import concurrency
from typing import List, Tuple
import ffmpeg
import re
import uuid


async def _run(pipeline):
    try:

        def _run_pipeline():
            pipeline.run(overwrite_output=True, capture_stderr=True)

        await concurrency.run_in_thread_pool(_run_pipeline)
    except ffmpeg.Error as e:
        raise RuntimeError(f"ffmpeg Error stderr: {e.stderr}")


def new_file(dir: str) -> Path:
    return Path(Path(dir) / f"freespeech.{uuid.uuid4()}")


async def write_streams(
    streams: list, extension: str, **kwargs
) -> Path:
    """writes a list of streams to a directory

    Args:
        streams: list of streams that'll be written to a file in output_dir
        output_dir: directory in which the file will be created.
        extension: file extension for the stream.
        args: optional, dict of args to pass into ffmpeg output.


    Return:
        The path of the file in the directory.
    """
    output_dir = "/tmp"
    output_file = Path(f"{new_file(output_dir)}.{extension}")
    pipeline = ffmpeg.output(*streams, **kwargs, filename=output_file)
    await _run(pipeline)

    return output_file


async def trim(audio: str, start_ms: int, end_ms: int) -> Path:
    """Trims audio to a given start and end time in milliseconds."""

    audio_stream = ffmpeg.input(audio).audio
    stream = audio_stream.filter_(
        "atrim", start=str(start_ms) + "ms", end=str(end_ms) + "ms"
    )

    return await write_streams(
        [stream],
        "wav",
        ac=1,  # audio channels = 1
        acodec="pcm_f32le",
        ar=22_050,
    )


async def extract_voices(events: List[Event], audio: str) -> List[Tuple[Voice, str]]:
    """Creates snippets of audio for each event in the list."""
    voices = []
    for event in events:
        voice = event.voice
        text = " ".join(event.chunks)
        split = re.split(r"#(\d+(\.\d+)?)#", text)
        sentences_and_pauses = list(zip_longest(split[0::3], split[1::3], fillvalue=""))
        if sentences_and_pauses[-1] == ("", ""):
            sentences_and_pauses.pop()
        if sentences_and_pauses[-1][-1] != "":
            tail_pause_ms = int(float(sentences_and_pauses[-1][-1]) * 1_000)
        else:
            tail_pause_ms = 0
        if event.duration_ms is not None:
            snippet = await trim(audio, event.time_ms, event.time_ms + event.duration_ms - tail_pause_ms)
            voices.append((voice, snippet))
    return voices 

In [25]:
from freespeech.api import transcript


_transcript = await transcript.load("https://docs.google.com/document/d/17cKE0V4I3u7O-2LLXtj4KmeMsYWsD2Ct7zUay8WBkrY/edit#")

In [26]:
audio_url = _transcript.audio
assert audio_url is not None, "Transcript doesn't have an audio track"
audio_file = f"/tmp/freespeech.{audio_url.split('/')[-1]}"

In [27]:
import zipfile
import os
from pathlib import Path


def package_voice_samples(samples: List[Tuple[Voice, str]]) -> List[str]:
    """Packages a list of voice samples into a zip file."""

    # group samples by voice
    samples_by_character = {}
    for voice, sample in samples:
        character = voice.character
        if character not in samples_by_character:
            samples_by_character[character] = []
        samples_by_character[character].append(sample)

    zip_files = []
    for character, files in samples_by_character.items():
        zip_file = Path("/tmp") / f"freespeech.{character}.{uuid.uuid4()}.zip"
        with zipfile.ZipFile(zip_file, "w") as zip:
            for file in files:
                print(f"Writing: {file.name}")
                zip.write(file, arcname=str(Path(character) / file.name))
        zip_files += [zip_file]
    return zip_files

In [28]:
!wget -O {audio_file}  {audio_url}

--2023-02-02 11:36:58--  https://storage.googleapis.com/freespeech-tests/media/c5c4b430-0547-4e23-bdae-b00f3d442705bzrjk8oh.x-wav
Resolving storage.googleapis.com (storage.googleapis.com)... 172.253.115.128, 172.253.122.128, 172.253.63.128, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|172.253.115.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 9491928 (9.1M) [application/octet-stream]
Saving to: ‘/tmp/freespeech.c5c4b430-0547-4e23-bdae-b00f3d442705bzrjk8oh.x-wav’

/tmp/freespeech.c5c 100%[===================>]   9.05M  51.1MB/s    in 0.2s    

2023-02-02 11:36:59 (51.1 MB/s) - ‘/tmp/freespeech.c5c4b430-0547-4e23-bdae-b00f3d442705bzrjk8oh.x-wav’ saved [9491928/9491928]



In [29]:
voice_samples = [event for event in _transcript.events if event.chunks != [""]]

In [30]:
res_2 = await extract_voices(voice_samples, audio_file)

In [31]:
import IPython.display as ipd
from IPython.display import HTML


display(HTML(f"<table>{''.join(f'<tr><td>{voice}</td><td>{path}</td><td>{ipd.Audio(path)._repr_html_()}</td></tr>' for voice, path in res_2)}</table>"))

In [32]:
res_2[:2]

[(Voice(character='Bill', pitch=0.0, speech_rate=1.0),
  PosixPath('/tmp/freespeech.5d8777fb-83c2-4690-9fff-d13206b77d48.wav')),
 (Voice(character='Bill', pitch=0.0, speech_rate=1.0),
  PosixPath('/tmp/freespeech.6a67a94b-0216-4b7b-8c3c-831a8d8df522.wav'))]

In [33]:
package_voice_samples(res + res_2[:2])

Writing: freespeech.a8297c83-4885-44ad-a809-e961b3966524.wav
Writing: freespeech.776b6504-e438-4654-831f-5907a521c5c1.wav
Writing: freespeech.aa0b35be-b055-4a02-a5f8-df3418f59c1d.wav
Writing: freespeech.5d8777fb-83c2-4690-9fff-d13206b77d48.wav
Writing: freespeech.6a67a94b-0216-4b7b-8c3c-831a8d8df522.wav


[PosixPath('/tmp/freespeech.Bill.683651c4-ba9d-4914-9d10-d38acb260768.zip')]

In [211]:
import zipfile


# extract zipfile into a directory
def extract_voices_zip(zip_file, output_dir: str) -> str:
    with zipfile.ZipFile(zip_file, "r") as zip_ref:
        zip_ref.extractall(output_dir)
    return str(output_dir)

In [213]:
extract_voices_zip(
    "/tmp/freespeech.Bill.be6d5845-dcf4-46eb-8fc6-ee7f27330c63.zip",
    output_dir="/tmp/Bill"    
)

'/tmp/Bill'

In [214]:
t = await transcript.load("https://docs.google.com/document/d/18jySMGhD_Xi_xwuNHXdaNRSWjYZN7S_A7MScuyeZEG0/edit#")

In [216]:
len([" ".join(event.chunks) for event in t.events if event.chunks != [""]])

51

In [34]:
from pathlib import Path


files = [(200, f"/home/astaff/Downloads/{index}.wav") for index in (0, 1, 2, 8)]

In [35]:
from freespeech.lib import media


res = await media.concat_and_pad(files, "/tmp/druma")

In [36]:
res

PosixPath('/tmp/druma/df4e47c9-fbb2-45dd-97c9-3bab2a8ca3fe.wav')

In [231]:
audio_url = "https://storage.googleapis.com/freespeech-tests/media/035e2d2c-f081-4edb-a95d-c97e93646cf9.webm"
video_url = "https://storage.googleapis.com/freespeech-tests/media/784ba948-fff0-4fe3-a30c-ddababe673bb.mp4"


In [37]:
from IPython.display import Audio

Audio("/tmp/druma/df4e47c9-fbb2-45dd-97c9-3bab2a8ca3fe.wav")

In [232]:
!wget -O /tmp/audio.webm {audio_url}
!wget -O /tmp/video.mp4 {video_url}

--2023-01-27 21:14:10--  https://storage.googleapis.com/freespeech-tests/media/035e2d2c-f081-4edb-a95d-c97e93646cf9.webm
Resolving storage.googleapis.com (storage.googleapis.com)... 142.251.111.128, 142.251.16.128, 142.251.163.128, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|142.251.111.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4178883 (4.0M) [video/webm]
Saving to: ‘/tmp/audio.webm’

/tmp/audio.webm     100%[===================>]   3.98M  --.-KB/s    in 0.1s    

2023-01-27 21:14:10 (37.4 MB/s) - ‘/tmp/audio.webm’ saved [4178883/4178883]

--2023-01-27 21:14:11--  https://storage.googleapis.com/freespeech-tests/media/784ba948-fff0-4fe3-a30c-ddababe673bb.mp4
Resolving storage.googleapis.com (storage.googleapis.com)... 172.253.122.128, 172.253.63.128, 172.253.115.128, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|172.253.122.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 34651332 

In [233]:
mixed = await media.mix(files=["/tmp/audio.webm", res], weights=[1, 10], output_dir="/tmp/")

In [235]:
await media.dub("/tmp/video.mp4", mixed, "/tmp/z")

PosixPath('/tmp/z/a22dc246-fe7e-4510-a5cc-9cf59a98fe3b.mp4')